In [1]:
!apt install swig cmake ffmpeg xvfb python3-opengl
!pip install stable-baselines3==2.0.0a5 gymnasium[box2d] huggingface_sb3 pyvirtualdisplay imageio[ffmpeg]

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
cmake is already the newest version (3.22.1-1ubuntu1.22.04.2).
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
The following additional packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 swig4.0 x11-xkb-utils xfonts-base
  xfonts-encodings xfonts-utils xserver-common
Suggested packages:
  libgle3 python3-numpy swig-doc swig-examples swig4.0-examples swig4.0-doc
The following NEW packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 python3-opengl swig swig4.0
  x11-xkb-utils xfonts-base xfonts-encodings xfonts-utils xserver-common xvfb
0 upgraded, 14 newly installed, 0 to remove and 45 not upgraded.
Need to get 9,755 kB of archives.
After this operation, 25.6 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 freeglut3 amd64 2.8.1-6 [74.0 kB]
Get:2 http://

In [ ]:
import os
os.kill(os.getpid(), 9)

In [1]:
from pyvirtualdisplay import Display
virtual_display = Display(visible=0, size=(1400, 900))
virtual_display.start()

In [2]:
import gymnasium as gym
env = gym.make("BipedalWalker-v3", hardcore=True)
env.reset()

(array([ 2.7469150e-03,  3.9839856e-06, -5.1948323e-04, -1.6000027e-02,
         9.2279390e-02,  1.2059489e-03,  8.6001837e-01,  4.4428682e-04,
         1.0000000e+00,  3.2650646e-02,  1.2059021e-03,  8.5364288e-01,
        -8.2057150e-04,  1.0000000e+00,  4.4081375e-01,  4.4581985e-01,
         4.6142250e-01,  4.8954991e-01,  5.3410250e-01,  6.0246068e-01,
         7.0914847e-01,  8.8593131e-01,  1.0000000e+00,  1.0000000e+00],
       dtype=float32),
 {})

In [3]:
print("_____OBSERVATION SPACE_____ \n")
print("Observation Space Shape", env.observation_space.shape)
print("Sample observation", env.observation_space.sample())

_____OBSERVATION SPACE_____ 

Observation Space Shape (24,)
Sample observation [ 2.5941279e+00 -3.7129135e+00  4.1753039e+00  2.4020288e+00
  2.7324817e+00  1.9422919e+00 -1.0294406e+00  1.9470292e+00
  1.8024154e+00  3.0276909e-01 -2.3600771e+00 -2.3969281e+00
  4.9673691e+00  5.8436710e-01 -9.9360384e-02 -6.4735021e-04
  7.4287331e-01 -8.7382692e-01  8.8109291e-01 -9.5015574e-01
 -5.2492219e-01 -5.2638775e-01  7.5352246e-01  4.9813081e-02]


In [4]:
print("\n _____ACTION SPACE_____ \n")
print("Action Space Shape", env.action_space.shape)
print("Action Space Sample", env.action_space.sample())


 _____ACTION SPACE_____ 

Action Space Shape (4,)
Action Space Sample [-0.6721563  -0.5757446  -0.51454055  0.1319156 ]


In [11]:
from stable_baselines3.common.env_util import make_vec_env
env = make_vec_env('BipedalWalker-v3', n_envs=1)

In [12]:
from stable_baselines3 import DDPG
model = DDPG(
    policy = 'MlpPolicy',
    env = env,
    buffer_size = 1000000,
    batch_size = 128,
    learning_rate = 0.001,
    gamma = 0.99,
    tau = 0.001,
    verbose=1)

Using cuda device


In [13]:
from wasabi import Printer
import numpy as np
from stable_baselines3.common.base_class import BaseAlgorithm
from pathlib import Path
import tempfile
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.vec_env import (
    DummyVecEnv,
    VecEnv,
    VecVideoRecorder,
)

msg = Printer()

In [14]:
def generate_replay(
    model: BaseAlgorithm,
    eval_env: VecEnv,
    video_length: int,
    is_deterministic: bool,
    local_path: Path,
):
    """
    Generate a replay video of the agent
    :param model: trained model
    :param eval_env: environment used to evaluate the agent
    :param video_length: length of the video (in timesteps)
    :param is_deterministic: use deterministic or stochastic actions
    :param local_path: path of the local repository
    """
    # This is another temporary directory for video outputs
    # SB3 created a -step-0-to-... meta files as well as other
    # artifacts which we don't want in the repo.
    with tempfile.TemporaryDirectory() as tmpdirname:
        # Step 1: Create the VecVideoRecorder
        env = VecVideoRecorder(
            eval_env,
            tmpdirname,
            record_video_trigger=lambda x: x == 0,
            video_length=video_length,
            name_prefix="",
        )

        obs = env.reset()
        lstm_states = None
        episode_starts = np.ones((env.num_envs,), dtype=bool)

        try:
            for _ in range(video_length):
                action, lstm_states = model.predict(
                    obs,
                    state=lstm_states,
                    episode_start=episode_starts,
                    deterministic=is_deterministic,
                )
                obs, _, episode_starts, _ = env.step(action)

            # Save the video
            env.close()

            # Convert the video with x264 codec
            inp = env.video_recorder.path
            out = local_path
            os.system(f"ffmpeg -y -i {inp} -vcodec h264 {out}".format(inp, out))
            print(f"Video saved to: {out}")
        except KeyboardInterrupt:
            pass
        except Exception as e:
            msg.fail(str(e))
            # Add a message for video
            msg.fail(
                "We are unable to generate a replay of your agent"
            )

In [15]:
import os
#create a directory to save the videos
video_dir = "/content/videos"
if not os.path.exists(video_dir):
    os.makedirs(video_dir)

In [16]:
env_id = "BipedalWalker-v3"
# Train and generate video at every 10000 steps, adjust the timesteps to your liking
for i in range(0, 200000, 10000):
    model.learn(total_timesteps=10000)
    # Save the model
    model_name = "ddpg-BipedalWalker-v3"
    model.save(model_name)
    video_name = f"replay_{i + 10000}.mp4"
    generate_replay(
        model=model,
        eval_env=DummyVecEnv([lambda: Monitor(gym.make(env_id, hardcore=True, render_mode="rgb_array"))]),
        video_length=1000,
        is_deterministic=True,
        local_path=os.path.join(video_dir, video_name)
    )

model_name = "ddpg-BipedalWalker-v3"
model.save(model_name)

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 838      |
|    ep_rew_mean     | -144     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 250      |
|    time_elapsed    | 13       |
|    total_timesteps | 3350     |
| train/             |          |
|    actor_loss      | -2.78    |
|    critic_loss     | 3.27     |
|    learning_rate   | 0.001    |
|    n_updates       | 1678     |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.03e+03 |
|    ep_rew_mean     | -151     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 153      |
|    time_elapsed    | 53       |
|    total_timesteps | 8255     |
| train/             |          |
|    actor_loss      | -0.491   |
|    critic_loss     | 0.0645   |
|    learning_rate   | 0.001    |
|    n_updates       | 8078     |
--------------

Moviepy - Done !
Moviepy - video ready /tmp/tmp4cxqq216/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_10000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 452      |
|    ep_rew_mean     | -125     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 773      |
|    time_elapsed    | 2        |
|    total_timesteps | 1810     |
| train/             |          |
|    actor_loss      | -1.48    |
|    critic_loss     | 2.34     |
|    learning_rate   | 0.001    |
|    n_updates       | 11494    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 646      |
|    ep_rew_mean     | -133     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 148      |
|    time_elapsed    | 34       |
|    total_timesteps | 5169     |
| train/             |          |
|    actor_loss     

Moviepy - Done !
Moviepy - video ready /tmp/tmpeqvh2pp7/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_20000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 64.2     |
|    ep_rew_mean     | -107     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 255      |
|    time_elapsed    | 1        |
|    total_timesteps | 257      |
| train/             |          |
|    actor_loss      | -0.973   |
|    critic_loss     | 1.94     |
|    learning_rate   | 0.001    |
|    n_updates       | 21430    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 59.1     |
|    ep_rew_mean     | -105     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 188      |
|    time_elapsed    | 2        |
|    total_timesteps | 473      |
| train/             |          |
|    actor_loss     

Moviepy - Done !
Moviepy - video ready /tmp/tmpy4wa0qsa/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_30000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 104      |
|    ep_rew_mean     | -116     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 314      |
|    time_elapsed    | 1        |
|    total_timesteps | 414      |
| train/             |          |
|    actor_loss      | -7.97    |
|    critic_loss     | 4.07     |
|    learning_rate   | 0.001    |
|    n_updates       | 31445    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 150      |
|    ep_rew_mean     | -117     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 191      |
|    time_elapsed    | 6        |
|    total_timesteps | 1200     |
| train/             |          |
|    actor_loss     

Moviepy - Done !
Moviepy - video ready /tmp/tmpiddmz0xy/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_40000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 158      |
|    ep_rew_mean     | -115     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 158      |
|    time_elapsed    | 3        |
|    total_timesteps | 631      |
| train/             |          |
|    actor_loss      | -9.11    |
|    critic_loss     | 5.95     |
|    learning_rate   | 0.001    |
|    n_updates       | 41814    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 111      |
|    ep_rew_mean     | -113     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 154      |
|    time_elapsed    | 5        |
|    total_timesteps | 888      |
| train/             |          |
|    actor_loss     

...

Moviepy - Done !
Moviepy - video ready /tmp/tmplxrtxmfq/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_160000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 464      |
|    ep_rew_mean     | -122     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 590      |
|    time_elapsed    | 3        |
|    total_timesteps | 1857     |
| train/             |          |
|    actor_loss      | -48.4    |
|    critic_loss     | 3.03     |
|    learning_rate   | 0.001    |
|    n_updates       | 167852   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 457      |
|    ep_rew_mean     | -124     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 148      |
|    time_elapsed    | 24       |
|    total_timesteps | 3654     |
| train/             |          |
|    actor_loss    

Moviepy - Done !
Moviepy - video ready /tmp/tmpf6rt0fcq/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_170000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 118      |
|    ep_rew_mean     | -119     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 212      |
|    time_elapsed    | 2        |
|    total_timesteps | 471      |
| train/             |          |
|    actor_loss      | -50.2    |
|    critic_loss     | 3.08     |
|    learning_rate   | 0.001    |
|    n_updates       | 177920   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 104      |
|    ep_rew_mean     | -117     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 184      |
|    time_elapsed    | 4        |
|    total_timesteps | 830      |
| train/             |          |
|    actor_loss    

Moviepy - Done !
Moviepy - video ready /tmp/tmpb0nmi029/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_180000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 533      |
|    ep_rew_mean     | -121     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 178      |
|    time_elapsed    | 11       |
|    total_timesteps | 2133     |
| train/             |          |
|    actor_loss      | -51.2    |
|    critic_loss     | 3.46     |
|    learning_rate   | 0.001    |
|    n_updates       | 189402   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 423      |
|    ep_rew_mean     | -134     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 169      |
|    time_elapsed    | 19       |
|    total_timesteps | 3381     |
| train/             |          |
|    actor_loss    

Moviepy - Done !
Moviepy - video ready /tmp/tmp_sxitkp2/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_190000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 113      |
|    ep_rew_mean     | -105     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 358      |
|    time_elapsed    | 1        |
|    total_timesteps | 451      |
| train/             |          |
|    actor_loss      | -53.2    |
|    critic_loss     | 5.02     |
|    learning_rate   | 0.001    |
|    n_updates       | 197795   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 248      |
|    ep_rew_mean     | -130     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 164      |
|    time_elapsed    | 12       |
|    total_timesteps | 1981     |
| train/             |          |
|    actor_loss    

Moviepy - Done !
Moviepy - video ready /tmp/tmpy8agbq9j/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_200000.mp4


In [17]:
with open(os.path.join(video_dir, "filelist.txt"), "w") as f:
    for i in range(0, 200000, 10000):
        video_name = f"replay_{i + 10000}.mp4"
        f.write(f"file '{os.path.join(video_dir, video_name)}'\n")
# Concatenate all the videos into one
os.system(f"ffmpeg -f concat -safe 0 -i {os.path.join(video_dir, 'filelist.txt')} -c copy {os.path.join(video_dir, 'replay_all.mp4')}")

0

In [18]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('videos/replay_all.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=600 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [19]:
from stable_baselines3.common.evaluation import evaluate_policy
eval_env = Monitor(gym.make("BipedalWalker-v3"))
mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10, deterministic=True)
print(f"mean_reward={mean_reward:.2f} +/- {std_reward}")

mean_reward=-148.26 +/- 22.853148470310334
